# BertSum

## Import library

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
PROJECT_ID = "/Projects/202011_DACON_Summarization"
ROOT_DIR = "/content/drive/MyDrive/Notebooks" + PROJECT_ID
DATA_DIR = ROOT_DIR + '/Datasets'
# IMAGES_PATH = ROOT_DIR + '/images'

In [ ]:
import numpy as np 
import pandas as pd
import os
import json

import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
sns.set(style='white', context='notebook', palette='deep')

import warnings
warnings.filterwarnings(action='ignore')

if get_ipython():
    print("jupyter envirionment")
    from tqdm import tqdm_notebook as tqdm  #이거 안해주면 한 줄씩 출력됨 ;;
else:
    print("command shell envirionment")
    from tqdm import tqdm

jupyter envirionment


In [ ]:
PROJECT_DIR = ROOT_DIR + '/PreSumm'
DATA_DIR = PROJECT_DIR + '/data'
RAW_DATA_DIR = DATA_DIR + '/raw'
JSON_DATA_DIR = DATA_DIR + '/json_data'
BERT_DATA_DIR = DATA_DIR + '/bert_data' 

MODEL_DIR = PROJECT_DIR + '/models'  
LOG_DIR = PROJECT_DIR + '/logs' # logs -> for storing logs information during preprocess and finetuning
RESULT_DIR = PROJECT_DIR + '/result' 

# MERGE_STORY_DIR = PreSumm_DATA_DIR + '/merged_stories_tokenized'  #  tokenized data  
# * **json_data** ->  json files
# * **bert_data** ->  .pt files
# * **logs** ->  for storing logs information during preprocess and finetuning
# * **temp** -> cache model config data
# * **bertsumextabs** ->  save finetuning model weights****

## Training

### 설치

In [ ]:
!pip install -r $PreSumm_DIR/requirements.txt

     |████████████████████████████████| 1.6MB 25.1MB/s 
     |████████████████████████████████| 20.4MB 1.4MB/s 
     |████████████████████████████████| 61kB 9.6MB/s 
     |████████████████████████████████| 184kB 6.7MB/s 
     |████████████████████████████████| 194kB 58.5MB/s 
     |████████████████████████████████| 676.9MB 24kB/s 
     |████████████████████████████████| 133kB 61.6MB/s 
     |████████████████████████████████| 71kB 10.9MB/s 
     |████████████████████████████████| 6.9MB 46.4MB/s 
  Created wheel for multiprocess: filename=multiprocess-0.70.9-cp36-none-any.whl size=100646 sha256=09562afcd1272b3b3295f8f1707e51d291d1d45106e08aa885fa82a3ca3a5d52
  Stored in directory: /root/.cache/pip/wheels/96/20/ac/9f1d164f7d81787cd6f4401b1d05212807d021fbbbcc301b82
  Created wheel for pyrouge: filename=pyrouge-0.1.3-cp36-none-any.whl size=191613 sha256=22723df0b7e04c50831643e4169114a5173e591a62c02d6be49dfc9c14d8d0b0
  Stored in directory: /root/.cache/pip/wheels/75/d3/0c/e5b04e15b6b87c42e9

In [ ]:
pip install transformers

     |████████████████████████████████| 1.3MB 19.9MB/s 
     |████████████████████████████████| 890kB 50.9MB/s 
     |████████████████████████████████| 1.1MB 50.5MB/s 
     |████████████████████████████████| 2.9MB 55.6MB/s 
  Created wheel for sacremoses: filename=sacremoses-0.0.43-cp36-none-any.whl size=893257 sha256=1a91ded3cdedd89582148fdd86c51ad32b9f173b4fa38684e83f0efcbaa88fae
  Stored in directory: /root/.cache/pip/wheels/29/3c/fd/7ce5c3f0666dab31a50123635e6fb5e19ceb42ce38d4e58f45
Successfully built sacremoses


In [ ]:
pip show transformers

Name: transformers
Version: 3.5.1
Summary: State-of-the-art Natural Language Processing for TensorFlow 2.0 and PyTorch
Home-page: https://github.com/huggingface/transformers
Author: Thomas Wolf, Lysandre Debut, Victor Sanh, Julien Chaumond, Sam Shleifer, Patrick von Platen, Sylvain Gugger, Google AI Language Team Authors, Open AI team Authors, Facebook AI Authors, Carnegie Mellon University Authors
Author-email: thomas@huggingface.co
License: Apache
Location: /usr/local/lib/python3.6/dist-packages
Requires: sacremoses, regex, filelock, numpy, sentencepiece, protobuf, tqdm, dataclasses, packaging, requests, tokenizers
Required-by: 


In [ ]:
!pip install kobert-transformers

In [ ]:
# !pip install tensorboardX 

### ㄴㅇㄹ

- presumm은 pytorch-transformer를 쓰고 있어서 kobert를 못가지고 옴. 다 바꿔줘야 함
- 이걸바꿔주다보니... 또 수정해야 할 곳들이 생기는듯

data_loader.py 내 다음 부분 수정해야함
```
# 이전
pts = sorted(glob.glob(args.bert_data_path + '.' + corpus_type + '.[0-9]*.pt'))
# 이후
    pts = sorted(glob.glob(args.bert_data_path + '/' + corpus_type + '.[0-9]*.pt'))
```


In [ ]:
%cd $PreSumm_DIR/src

/content/drive/MyDrive/Notebooks/Projects/202011_DACON_Summarization/PreSumm/src


In [ ]:
# python train.py -task ext -mode train -bert_data_path BERT_DATA_PATH -ext_dropout 0.1 -model_path MODEL_PATH -lr 2e-3 -visible_gpus 0,1,2 -report_every 50 -save_checkpoint_steps 1000 -batch_size 3000 -train_steps 50000 -accum_count 2 -log_file ../logs/ext_bert_cnndm -use_interval true -warmup_steps 10000 -max_pos 512
 # !python train.py  -task abs -mode train -train_from /kaggle/input/absbert-weights/model_step_149000.pt -bert_data_path /kaggle/working/bert_data/news  -dec_dropout 0.2  -model_path /kaggle/working/bertsumextabs -sep_optim true -lr_bert 0.002 -lr_dec 0.02 -save_checkpoint_steps 1000 -batch_size 140 -train_steps 150000 -report_every 100 -accum_count 5 -use_bert_emb true -use_interval true -warmup_steps_bert 1000 -warmup_steps_dec 500 -max_pos 512 -visible_gpus 0  -temp_dir /kaggle/working/temp -log_file /kaggle/working/logs/abs_bert_cnndm

In [ ]:
!python "train.py" -task ext -mode train \
                    -bert_data_path $BERT_DATA_DIR -model_path $MODEL_DIR -log_file $LOG_FILE \
                     -ext_dropout 0.1 -lr 2e-3 -visible_gpus 0 -report_every 50 -save_checkpoint_steps 200 -batch_size 500 -train_steps 5000 -accum_count 2 -use_interval true -warmup_steps 3000 -max_pos 512

2020-11-30 10:48:17.315421: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
[2020-11-30 10:48:28,447 INFO] Device ID 0
[2020-11-30 10:48:29,283 INFO] Device cuda
[2020-11-30 10:48:49,583 INFO] ExtSummarizer(
  (bert): Bert(
    (model): BertModel(
      (embeddings): BertEmbeddings(
        (word_embeddings): Embedding(8002, 768, padding_idx=1)
        (position_embeddings): Embedding(512, 768)
        (token_type_embeddings): Embedding(2, 768)
        (LayerNorm): LayerNorm(torch.Size([768]), eps=1e-12, elementwise_affine=True)
        (dropout): Dropout(p=0.1)
      )
      (encoder): BertEncoder(
        (layer): ModuleList(
          (0): BertLayer(
            (attention): BertAttention(
              (self): BertSelfAttention(
                (query): Linear(in_features=768, out_features=768, bias=True)
                (key): Linear(in_features=768, out_features=768, bias=True)
                (value): Linear(i

## Test

In [ ]:
!pip install -r $PreSumm_DIR/requirements.txt

In [ ]:
pip install transformers==3.5.1

     |████████████████████████████████| 1.3MB 6.0MB/s 
     |████████████████████████████████| 2.9MB 18.4MB/s 
     |████████████████████████████████| 1.1MB 42.0MB/s 
  Found existing installation: tokenizers 0.9.4
    Uninstalling tokenizers-0.9.4:
      Successfully uninstalled tokenizers-0.9.4
  Found existing installation: sentencepiece 0.1.94
    Uninstalling sentencepiece-0.1.94:
      Successfully uninstalled sentencepiece-0.1.94
  Found existing installation: transformers 4.0.0
    Uninstalling transformers-4.0.0:
      Successfully uninstalled transformers-4.0.0


In [ ]:
!pip show transformers

Name: transformers
Version: 3.5.1
Summary: State-of-the-art Natural Language Processing for TensorFlow 2.0 and PyTorch
Home-page: https://github.com/huggingface/transformers
Author: Thomas Wolf, Lysandre Debut, Victor Sanh, Julien Chaumond, Sam Shleifer, Patrick von Platen, Sylvain Gugger, Google AI Language Team Authors, Open AI team Authors, Facebook AI Authors, Carnegie Mellon University Authors
Author-email: thomas@huggingface.co
License: Apache
Location: /usr/local/lib/python3.6/dist-packages
Requires: packaging, regex, sentencepiece, sacremoses, filelock, dataclasses, numpy, requests, protobuf, tqdm, tokenizers
Required-by: 


In [ ]:
%cd $PreSumm_DIR/src

/content/drive/MyDrive/Notebooks/Projects/202011_DACON_Summarization/PreSumm/src


In [ ]:
# # !python train.py -task abs -mode test -model_path /kaggle/working/bertsumextabs -test_from /kaggle/working/bertsumextabs/model_step_150000.pt -batch_size 100 -test_batch_size 100 -bert_data_path /kaggle/working/bert_data/news -temp_dir /kaggle/working/temp -log_file /kaggle/working/logs/abs_bert_cnndm  -sep_optim true -use_interval true -visible_gpus 0 -max_pos 512 -max_length 200 -alpha 0.82 -min_length 10 -result_path /kaggle/working/logs/abs_bert_cnndm

In [ ]:
# !pip install pyrouge --upgrade
# !pip install https://github.com/bheinzerling/pyrouge/archive/master.zip
# !pip install pyrouge
# !pip show pyrouge
# !git clone https://github.com/andersjo/pyrouge.git
# !pyrouge_set_rouge_path 'pyrouge/tools/ROUGE-1.5.5'

In [ ]:
!python train.py -task ext -mode test \
                -test_from $MODEL_DIR/extract/model_step_4600.pt \
                -bert_data_path $BERT_DATA_DIR -model_path $MODEL_DIR -log_file $PreSumm_DIR/logs/val_abs_bert_cnndm \
                -test_batch_size 1  -batch_size 300 \
                -sep_optim true -use_interval true -visible_gpus 0 -max_pos 512 -max_length 200 -alpha 0.95 -min_length 50 -result_path $PreSumm_DIR/logs/abs_bert_cnndm \
                -report_rouge False
                 # -batch_size 300 

Streaming output truncated to the last 5000 lines.
selected_ids:  [[ 0  1  2  3  4  5  6  7  9  8 10]]
batch.src_str[i]:  ['수원시 는 오 는 1 2 일 오전 1 1 시 화장실 문화 전시관 해우 재 잔디 마당 · 야외 공원 에서 ‘ 제 8 회 해 우재 황금 똥 그림 잔치 ’ 를 연다고 7 일 밝혔 다 .', '해 우재 는 2 0 1 2 년 부터 매년 1 0 월 ‘ 황금 똥 그림 잔치 ’ 를 열 고 어린이 를 위한 그림 대회 , 마술 쇼 , 동요 공연 등 다채 로운 프로그램 을 진행 하 고 있 다 .', '올해 는 ▶ 어린이 그림 대회 ▶ 생태 체험 미술 부스 ▶ 함께 만드 는 컬러 풀 , 원더풀 ( colorful , wonderful ) 해 우재 ▶ 손 씻 기 캠페인 등 으로 진행 된다 .', '어린이 그림 대회 주제 는 ‘ 황금 똥 · 해 우재 · 화장실 ’ 이 다 .', '유 치부 · 초등 부 어린이 누구 나 무료 로 참여 할 수 있 다 .', '해우 재 홈페이지 ‘ 교육 신청 → 황금 똥 그림 잔치 ’ 에서 8 일 까지 신청 하 면 된다 .', '생태 체험 미술 부스 에서 는 화장실 · 자원 순환 등 을 주제 로 한 미술 활동 을 할 수 있 다 .', '손 씻 기 캠페인 에 는 대학생 들 이 참가 해 ‘ 세계 손 씻 기 의 날 ( 10 월 1 5 일 ) ’ 과 ‘ 손 씻 기 의 중요 성 ’ 등 을 알릴 예정 이 다 .', '함께 만드 는 컬러 풀 , 원더풀 해 우재 는 참가자 전원 이 대형 해우 재 그림 을 완성 하 는 협동 미술 프로젝트 다 .', '이 밖 에 마술 쇼 , 동요 공연 , 페이스 페인팅 , 보물찾기 등 프로그램 이 운영 된다 .', '시 관계자 는 " 올해 축제 는 어린이 들 의 상상 력 을 자극 하 는 다채 로운 프로그램 으로 구성 됐 다 " 며 " 어린이 와 시민 들 이 친근 하 게 느낄 수 있 는 ‘ 화장실 문화 ’ 를 조성 하 기 위해

## submission

In [ ]:
# test set
with open(RAW_DATA_DIR + '/ext/extractive_test_v2.jsonl', 'r') as json_file:
    json_list = list(json_file)

tests = []
for json_str in json_list:
    line = json.loads(json_str)
    tests.append(line)

test_df = pd.DataFrame(tests)
test_df

media         id                                   article_original
0     당진시대  500733466  [▲ 석문간척지 임차법인협의회가 한국농어촌공사 당진지사 앞에 공공비축벼 320t을 ...
1     당진시대  500742482  [신 벌떼해장국이 손님들의 성원에 보답하고자 24시간 영업을 재개한다., 또한 이와...
2     당진시대  500742484  [1년 전과 비교해 당진지역 휘발유 가격은 72원, 경유 가격은 103원 상승했다....
3     당진시대  504213810  [어기구 국회의원이 천연가스의 안정적 수급을 위해 2020년 착공이 예정돼 있는 액...
4     당진시대  505279620  [당진시정책자문위원회가 유명무실하다는 비판이 지속적으로 제기되고 있다., 민선6기가...
...    ...        ...                                                ...
9982  기호일보  745338220  [지지부진한 인천 내항 재개발사업의 물꼬를 터 줄 것으로 기대했던 도시재생 혁신지구...
9983  광주일보  745367988  [청와대는 30일 문재인 대통령의 ‘1호 공약’인 고위공직자범죄수사처(공수처) 설치...
9984  광주일보  745368130  [광주지역 광공업 생산 감소율이 14개월 만에 최고를 기록했다., 기아자동차 광주공...
9985  광주일보  745368136  [아름다운 가게 용봉점 헌책방이 개점 10년만에 문을 닫는 다., 올해 열렸던 10...
9986  광주일보  745368284  [현대차그룹은 최근 한국렌터카사업조합연합회와 ‘미래 모빌리티 사업 협력을 위한 양해...

[9987 rows x 3 columns]

In [ ]:
with open(PreSumm_DIR + '/logs/abs_bert_cnndm_step4600.candidate', 'r') as file:
    lines = file.readlines()
# print(lines)
test_pred_list = []
for line in lines:
    sum_sents_text, sum_sents_idxes = line.rsplit(r'[', maxsplit=1)
    sum_sents_text = sum_sents_text.replace('<q>', '\n')
    sum_sents_idx_list = [ int(str.strip(i)) for i in sum_sents_idxes[:-2].split(', ')]
    test_pred_list.append({'sum_sents_tokenized': sum_sents_text, 
                          'sum_sents_idxes': sum_sents_idx_list
                           })
test_pred_list

[{'sum_sents_idxes': [1, 2, 4],
  'sum_sents_tokenized': '석문 간척지 임차 법인 협의회 ( 이하 간척지 협의회 ) 가 농림 축산 식품 부 의 부당 한 간척지 임대료 책정 에 반발 하 며 지난달 3 0 일 한국 농어촌 공사 당진 지사 앞 에 공공 비축 벼 3 2 0 t 을 쌓 고 시위 를 벌였 다 .\n43 개 영농 조합 법인 이 소속 된 간척지 협의회 는 이번 벼 야적 시위 를 통해 현재 1 kg 당 2 1 0 0 원 으로 책정 된 임대료 를 현재 쌀 판매 가격 인 1 3 0 0 원대 로 인하 할 것 을 요구 하 고 있 다 .\n게다가 임차 법인 들 의 계약 기간 이 올해 만료 되 기 때문 에 임대료 를 인하 해도 지난 2 년 동안 의 손실 보상 은 받 을 수 없 는 상황 이 다 .'},
 {'sum_sents_idxes': [1, 0, 2],
  'sum_sents_tokenized': '또한 이 와 함께 오 는 1 2 일 부터 3 1 일 까지 특별 감사 이벤트 를 실시 할 예정 이 다 .\n신 벌 떼 해장국 이 손님 들 의 성원 에 보답 하 고자 2 4 시간 영업 을 재개 한다 .\n이 기간 동안 야간 ( 저녁 1 1 시 ~ 오전 7 시 ) 에 찾 는 손님 들 을 위해 뼈 해장국 은 2 0 0 0 원 , 감자탕 은 5 0 0 0 원 할인 된 가격 으로 제공 한다 .'},
 {'sum_sents_idxes': [1, 3, 8],
  'sum_sents_tokenized': '지난해 1 월 1 4 일 기준 으로 당진 지역 의 평균 휘발유 가격 이 1 4 1 8 원 , 경유 1 1 9 7 원 이 었 던 반면 , 올해 에 는 지난 4 일 기준 으로 휘발유 1 4 9 0 원 , 경유 1 3 0 0 원 인 것 으로 조사 됐 다 .\n반면 면천면 휘발유 평균 가격 은 1 4 7 8 원 으로 가장 낮 았 으며 , 경유 는 정미면 이 평균 가격 1 2 5 4 원 으로 가장 저렴 했 다 .\n유류 가격 은 읍 · 면 · 동 별 

In [ ]:
result_df = pd.merge(test_df, pd.DataFrame(test_pred_list), how="left", left_index=True, right_index=True)
result_df['summary'] = result_df.apply(lambda row: '\n'.join(list(np.array(row['article_original'])[row['sum_sents_idxes']])) , axis=1)
result_df

media  ...                                            summary
0     당진시대  ...  석문간척지 임차법인협의회(이하 간척지협의회)가 농림축산식품부의 부당한 간척지 임대료...
1     당진시대  ...  또한 이와 함께 오는 12일부터 31일까지 특별 감사 이벤트를 실시할 예정이다.\n...
2     당진시대  ...  지난해 1월 14일 기준으로 당진지역의 평균 휘발유 가격이 1418원, 경유 119...
3     당진시대  ...  어기구 국회의원이 천연가스의 안정적 수급을 위해 2020년 착공이 예정돼 있는 액화...
4     당진시대  ...  민선6기가 출범하면서 김홍장 당진시장이 정책 수립 과정에서 각계 전문가의 의견을 수...
...    ...  ...                                                ...
9982  기호일보  ...  보도에 따르면 최근 국토교통부 도시재생특별위원회 심의 결과 인천시가 신청한 내항1부...
9983  광주일보  ...  청와대는 30일 문재인 대통령의 ‘1호 공약’인 고위공직자범죄수사처(공수처) 설치법...
9984  광주일보  ...  30일 호남지방통계청이 발표한 ‘11월 산업활동동향’에 따르면 광주 광공업생산지수는...
9985  광주일보  ...  “10년 동안 참 고마웠습니다.”\n광주시 북구 용봉동 ‘아름다운 가게’ 용봉점 헌...
9986  광주일보  ...  다만, 쏘카와 같이 카세어링에 직접 진출하는 것이 아니라, 렌터카업체들이 이 시장에...

[9987 rows x 6 columns]

In [ ]:
submit_df = pd.read_csv(DATA_DIR + '/추출요약/extractive_sample_submission_v2.csv')
submit_df

id              summary
0     500733466  추출요약1\n추출요약2\n추출요약3
1     500742482  추출요약1\n추출요약2\n추출요약3
2     500742484  추출요약1\n추출요약2\n추출요약3
3     504213810  추출요약1\n추출요약2\n추출요약3
4     505279620  추출요약1\n추출요약2\n추출요약3
...         ...                  ...
9982  745338220  추출요약1\n추출요약2\n추출요약3
9983  745367988  추출요약1\n추출요약2\n추출요약3
9984  745368130  추출요약1\n추출요약2\n추출요약3
9985  745368136  추출요약1\n추출요약2\n추출요약3
9986  745368284  추출요약1\n추출요약2\n추출요약3

[9987 rows x 2 columns]

In [ ]:
submit_df.drop(['summary'], axis=1, inplace=True)

In [ ]:
print(result_df['id'].dtypes)
print(submit_df.dtypes)

result_df['id'] = result_df['id'].astype(int)
print(result_df['id'].dtypes)

object
id    int64
dtype: object
int64


In [ ]:
submit_df  = pd.merge(submit_df, result_df.loc[:, ['id', 'summary']], how="left", left_on="id", right_on="id")
submit_df

id                                            summary
0     500733466  석문간척지 임차법인협의회(이하 간척지협의회)가 농림축산식품부의 부당한 간척지 임대료...
1     500742482  또한 이와 함께 오는 12일부터 31일까지 특별 감사 이벤트를 실시할 예정이다.\n...
2     500742484  지난해 1월 14일 기준으로 당진지역의 평균 휘발유 가격이 1418원, 경유 119...
3     504213810  어기구 국회의원이 천연가스의 안정적 수급을 위해 2020년 착공이 예정돼 있는 액화...
4     505279620  민선6기가 출범하면서 김홍장 당진시장이 정책 수립 과정에서 각계 전문가의 의견을 수...
...         ...                                                ...
9982  745338220  보도에 따르면 최근 국토교통부 도시재생특별위원회 심의 결과 인천시가 신청한 내항1부...
9983  745367988  청와대는 30일 문재인 대통령의 ‘1호 공약’인 고위공직자범죄수사처(공수처) 설치법...
9984  745368130  30일 호남지방통계청이 발표한 ‘11월 산업활동동향’에 따르면 광주 광공업생산지수는...
9985  745368136  “10년 동안 참 고마웠습니다.”\n광주시 북구 용봉동 ‘아름다운 가게’ 용봉점 헌...
9986  745368284  다만, 쏘카와 같이 카세어링에 직접 진출하는 것이 아니라, 렌터카업체들이 이 시장에...

[9987 rows x 2 columns]

In [ ]:
submit_df.isnull().sum()

id         0
summary    0
dtype: int64

In [ ]:
import time
now = time.strftime('%y%m%d_%H%M')

submit_df.to_csv(DATA_DIR + f'/추출요약/submission_{now}.csv', index=False, encoding="utf-8-sig")

'201130_070702'

In [ ]:
!pip install pyrouge --upgrade

Requirement already up-to-date: pyrouge in /usr/local/lib/python3.6/dist-packages (0.1.3)


In [ ]:
!pip show pyrouge

Name: pyrouge
Version: 0.1.3
Summary: A Python wrapper for the ROUGE summarization evaluation package.
Home-page: https://github.com/noutenki/pyrouge
Author: Benjamin Heinzerling, Anders Johannsen
Author-email: benjamin.heinzerling@h-its.org
License: LICENSE.txt
Location: /usr/local/lib/python3.6/dist-packages
Requires: 
Required-by: 


In [ ]:
                #-test_from /kaggle/working/bertsumextabs/model_step_150000.pt

In [ ]:
-model_path /kaggle/working/bertsumextabs -test_from /kaggle/working/bertsumextabs/model_step_150000.pt -batch_size 100 -test_batch_size 100 -bert_data_path /kaggle/working/bert_data/news -temp_dir /kaggle/working/temp -log_file /kaggle/working/logs/abs_bert_cnndm  -sep_optim true -use_interval true -visible_gpus 0 -max_pos 512 -max_length 200 -alpha 0.82 -min_length 10 -result_path /kaggle/working/logs/abs_bert_cnndm

In [ ]:
!python train.py -task ext -mode test \
                -test_from $MODEL_DIR/model_step_1800.pt \
                -bert_data_path $BERT_DATA_DIR -model_path $MODEL_DIR -log_file $PreSumm_DIR/logs/val_abs_bert_cnndm \
                -batch_size 100 -test_batch_size 100  -sep_optim true -use_interval true -visible_gpus 0 -max_pos 512 -max_length 200 -alpha 0.95 -min_length 50 -result_path $PreSumm_DIR/logs/abs_bert_cnndm

2020-12-02 19:06:07.604377: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
[2020-12-02 19:06:10,978 INFO] Loading checkpoint from /content/drive/MyDrive/Notebooks/Projects/202011_DACON_Summarization/PreSumm/models/model_step_1800.pt
Namespace(accum_count=1, alpha=0.95, batch_size=100, beam_size=5, bert_data_path='/content/drive/MyDrive/Notebooks/Projects/202011_DACON_Summarization/PreSumm/data/bert_data', beta1=0.9, beta2=0.999, block_trigram=True, dec_dropout=0.2, dec_ff_size=2048, dec_heads=8, dec_hidden_size=768, dec_layers=6, enc_dropout=0.2, enc_ff_size=512, enc_hidden_size=512, enc_layers=6, encoder='bert', ext_dropout=0.2, ext_ff_size=2048, ext_heads=8, ext_hidden_size=768, ext_layers=2, finetune_bert=True, generator_shard_size=32, gpu_ranks=[0], label_smoothing=0.1, large=False, load_from_extractive='', log_file='/content/drive/MyDrive/Notebooks/Projects/202011_DACON_Summarization/PreSumm/logs/val_abs_bert_c

In [ ]:
with open(RAW_DATA_DIR + '/ext/train.jsonl', 'r') as json_file:
    json_list = list(json_file)

trains = []
for json_str in json_list:
    line = json.loads(json_str)
    trains.append(line)

In [ ]:
train_df = pd.DataFrame(trains)
train_df

media  ...  extractive
0      당진시대  ...   [0, 1, 2]
1      국제신문  ...   [0, 1, 3]
2      기호일보  ...  [6, 7, 10]
3      대구일보  ...   [1, 6, 4]
4      대구신문  ...  [2, 3, 10]
...     ...  ...         ...
42798  대구신문  ...   [0, 1, 2]
42799  대구일보  ...   [1, 2, 4]
42800  기호일보  ...   [2, 3, 6]
42801  당진시대  ...   [4, 6, 0]
42802  대전일보  ...   [2, 5, 4]

[42803 rows x 5 columns]

In [ ]:
 train_df.sample(frac=0.95,random_state=42) #random state is a seed value
test=df.drop(train.index)

media  ...   extractive
1291     광주일보  ...    [0, 5, 6]
25526  광주매일신문  ...  [26, 1, 34]
41099    남도일보  ...   [2, 4, 11]
21640    남도일보  ...    [2, 3, 5]
3308     기호일보  ...    [0, 1, 3]
...       ...  ...          ...
23429    경기일보  ...    [0, 6, 7]
35298    기호일보  ...  [10, 4, 16]
11138    광주일보  ...    [0, 1, 2]
14716    당진시대  ...    [0, 1, 2]
8429     대전일보  ...    [0, 2, 3]

[40663 rows x 5 columns]

In [ ]:
from transformers import BertModel
bert_model = BertModel.from_pretrained("monologg/kobert")


In [ ]:
!ls

cal_rouge.py	models	       preprocess.py	     train_extractive.py
distributed.py	others	       __pycache__	     train.py
logs		post_stats.py  traced_bert.pt	     translate
MODEL_PATH	prepro	       train_abstractive.py


In [ ]:
bert_model.embeddings.word_embeddings


# from transformers import AutoModelWithLMHead, AutoTokenizer

# model = AutoModelWithLMHead.from_pretrained("t5-base", return_dict=True)
# >>> tokenizer = AutoTokenizer.from_pretrained("t5-base")

# >>> # T5 uses a max_length of 512 so we cut the article to 512 tokens.
# >>> inputs = tokenizer.encode("summarize: " + ARTICLE, return_tensors="pt", max_length=512)
# >>> outputs = model.generate(inputs, max_length=150, min_length=40, length_penalty=2.0, num_beams=4, early_stopping=True)

In [ ]:
pip list -v | grep -F kobert-transformers

kobert-transformers           0.4.1           /usr/local/lib/python3.6/dist-packages pip      


In [ ]:
!ls /usr/local/lib/python3.6/dist-packages/kobert_transformers

__init__.py  load_model.py  __pycache__  tokenization_kobert.py  utils.py


In [ ]:
from kobert_transformers.tokenization_kobert import KoBertTokenizer
bert_tokenizer = KoBertTokenizer.from_pretrained('monologg/kobert') # monologg/distilkobert도 동일
print(bert_tokenizer.tokenize("[CLS] 한국어 모델을 공유합니다. [SEP]"))
print(bert_tokenizer.convert_tokens_to_ids(['[CLS]', '▁한국', '어', '▁모델', '을', '▁공유', '합니다', '.', '[SEP]']))


['[CLS]', '▁한국', '어', '▁모델', '을', '▁공유', '합니다', '.', '[SEP]']
[2, 4958, 6855, 2046, 7088, 1050, 7843, 54, 3]


In [ ]:
ARTICLE = "[CLS] 한국어 모델을 공유합니다. 한국어 모델을 공유합니다.한국어 모델을 공유합니다.한국어 모델을 공유합니다.한국어 모델을 공유합니다.한국어 모델을 공유합니다.한국어 모델을 공유합니다.[SEP]"
inputs = bert_tokenizer.encode("summarize: " + ARTICLE, return_tensors="pt", max_length=512)
outputs = bert_model.generate(inputs, max_length=150, min_length=5, length_penalty=2.0, num_beams=4, early_stopping=True, truncation=True, return_dict=True)
outputs

AttributeError: ignored

In [ ]:
from transformers import BertTokenizer, BertModel
tokenizer = BertTokenizer.from_pretrained("monologg/kobert")

tokenizer = BertTokenizer.from_pretrained("monologg/kobert")
model = BertModel.from_pretrained("monologg/kobert", return_dict=True)

inputs = tokenizer("Hello, my dog is cute", return_tensors="pt")
outputs = model(**inputs)
outputs

In [ ]:

>>> last_hidden_states = outputs.last_hidden_state

In [ ]:
inputs

tensor([[   2,  517,  440,  448,  423,  375,  405,  459,  389,  249,    2, 4958,
         6855, 2046, 7088, 1050, 7843,   54, 4958, 6855, 2046, 7088, 1050, 7843,
           54, 7829, 6855, 2046, 7088, 1050, 7843,   54, 7829, 6855, 2046, 7088,
         1050, 7843,   54, 7829, 6855, 2046, 7088, 1050, 7843,   54, 7829, 6855,
         2046, 7088, 1050, 7843,   54, 7829, 6855, 2046, 7088, 1050, 7843,   54,
            3,    3]])

# 이전

### kobertfmf torch script 파일(.pt)로 export하기(안해도됨)

In [ ]:
%cd $PreSumm_DIR/src

/content/drive/MyDrive/Notebooks/Projects/202011_DACON_Summarization/PreSumm/src


In [ ]:
!ls

cal_rouge.py	MODEL_PATH  post_stats.py  __pycache__		 train.py
distributed.py	models	    prepro	   train_abstractive.py  translate
logs		others	    preprocess.py  train_extractive.py


In [ ]:
from transformers import BertModel, BertTokenizer, BertConfig
import torch

enc = BertTokenizer.from_pretrained("monologg/kobert")

# Tokenizing input text
text = "[CLS] Who was Jim Henson ? [SEP] Jim Henson was a puppeteer [SEP]"
tokenized_text = enc.tokenize(text)

# Masking one of the input tokens
masked_index = 8
tokenized_text[masked_index] = '[MASK]'
indexed_tokens = enc.convert_tokens_to_ids(tokenized_text)
segments_ids = [0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1]

# Creating a dummy input
tokens_tensor = torch.tensor([indexed_tokens])
segments_tensors = torch.tensor([segments_ids])
dummy_input = [tokens_tensor, segments_tensors]



# If you are instantiating the model with `from_pretrained` you can also easily set the TorchScript flag
model = BertModel.from_pretrained("monologg/kobert", torchscript=True)

# Creating the trace
traced_model = torch.jit.trace(model, [tokens_tensor, segments_tensors])
torch.jit.save(traced_model, MODEL_DIR + "/traced_bert.pt")

### 가볍게 bert 기반 summarizairion 하기


https://www.kaggle.com/pemagrg/text-summarization-using-bert-gpt2-xlnet

In [ ]:
!pip install bert-extractive-summarizer

In [ ]:
!pip install transformers==2.2.0

In [ ]:
!pip install spacy==2.0.12

In [ ]:
from summarizer import Summarizer,TransformerSummarizer

BERT Summarizer

In [ ]:
bert_model = Summarizer()

In [ ]:
for doc in train_df['article_original'].values:
    bert_summary = ''.join(bert_model(body, min_length=60))

In [ ]:
bert_summary = ''.join(bert_model(body, min_length=60))
print(bert_summary)

**GPT2_model**

In [ ]:

GPT2_model = TransformerSummarizer(transformer_type="GPT2",transformer_model_key="gpt2-medium")
full = ''.join(GPT2_model(body, min_length=60))
print(full)

**XLNet**

In [ ]:
model = TransformerSummarizer(transformer_type="XLNet",transformer_model_key="xlnet-base-cased")
full = ''.join(model(body, min_length=60))
print(full)